In [1]:
import os
import numpy as np
import matplotlib.pyplot as plt
import nibabel as nib
from nilearn import datasets, plotting
from nilearn.image import math_img
from nilearn import plotting, datasets
import nilearn
import nibabel as nib
from nibabel.testing import data_path
#from gifti_io import read_gifti, write_gifti

/home/subbainria/anaconda3/lib/python3.8/site-packages/nilearn/datasets/__init__.py:86: FutureWarning: Fetchers from the nilearn.datasets module will be updated in version 0.9 to return python strings instead of bytes and Pandas dataframes instead of Numpy arrays.
  warn("Fetchers from the nilearn.datasets module will be "


In [2]:
# The download cells will store the data in nested directories starting here:
HCP_DIR = "./hcp"
if not os.path.isdir(HCP_DIR):
  os.mkdir(HCP_DIR)

# The data shared for NMA projects is a subset of the full HCP dataset
N_SUBJECTS = 339

# The data have already been aggregated into ROIs from the Glasser parcellation
N_PARCELS = 360

# The acquisition parameters for all tasks were identical
TR = 0.72  # Time resolution, in seconds

# The parcels are matched across hemispheres with the same order
HEMIS = ["Right", "Left"]

# Each experiment was repeated twice in each subject
N_RUNS = 2

# There are 7 tasks. Each has a number of 'conditions'

EXPERIMENTS = {
    'MOTOR'      : {'runs': [5,6],   'cond':['lf','rf','lh','rh','t','cue']},
    'WM'         : {'runs': [7,8],   'cond':['0bk_body','0bk_faces','0bk_places','0bk_tools','2bk_body','2bk_faces','2bk_places','2bk_tools']},
    'EMOTION'    : {'runs': [9,10],  'cond':['fear','neut']},
    'GAMBLING'   : {'runs': [11,12], 'cond':['loss','win']},
    'LANGUAGE'   : {'runs': [13,14], 'cond':['math','story']},
    'RELATIONAL' : {'runs': [15,16], 'cond':['match','relation']},
    'SOCIAL'     : {'runs': [17,18], 'cond':['mental','rnd']}
}

# You may want to limit the subjects used during code development.
# This will use all subjects:
subjects = range(N_SUBJECTS)

In [3]:
from nilearn import plotting, datasets

# NMA provides an atlas 
fname = f"{HCP_DIR}/hcp_atlas.npz"
if not os.path.exists(fname):
  !wget -qO $fname https://osf.io/j5kuc/download
with np.load(fname) as dobj:
  atlas = dict(**dobj)

# Try both hemispheres (L->R and left->right)
fsaverage = datasets.fetch_surf_fsaverage(mesh='fsaverage6')

In [4]:
fsaverage.keys()

dict_keys(['area_left', 'area_right', 'curv_left', 'curv_right', 'infl_left', 'infl_right', 'pial_left', 'pial_right', 'sphere_left', 'sphere_right', 'sulc_left', 'sulc_right', 'thick_left', 'thick_right', 'white_left', 'white_right', 'description'])

In [47]:
L_labels = nib.load('./tpl-fsaverage6/tpl-fsaverage6_hemi-L_desc-MMP_dseg.label.gii')
R_labels = nib.load('./tpl-fsaverage6/tpl-fsaverage6_hemi-R_desc-MMP_dseg.label.gii')

In [37]:
L_labels.get_labeltable().get_labels_as_dict()

<ipython-input-37-3df3d859602e>:1: DeprecationWarning: get_labeltable method deprecated. Use the gifti_img.labeltable property instead.

* deprecated from version: 2.1
* Will raise <class 'nibabel.deprecator.ExpiredDeprecationError'> as of version: 4.0
  L_labels.get_labeltable().get_labels_as_dict()


{0: '???',
 1: 'L_V1_ROI',
 2: 'L_MST_ROI',
 3: 'L_V6_ROI',
 4: 'L_V2_ROI',
 5: 'L_V3_ROI',
 6: 'L_V4_ROI',
 7: 'L_V8_ROI',
 8: 'L_4_ROI',
 9: 'L_3b_ROI',
 10: 'L_FEF_ROI',
 11: 'L_PEF_ROI',
 12: 'L_55b_ROI',
 13: 'L_V3A_ROI',
 14: 'L_RSC_ROI',
 15: 'L_POS2_ROI',
 16: 'L_V7_ROI',
 17: 'L_IPS1_ROI',
 18: 'L_FFC_ROI',
 19: 'L_V3B_ROI',
 20: 'L_LO1_ROI',
 21: 'L_LO2_ROI',
 22: 'L_PIT_ROI',
 23: 'L_MT_ROI',
 24: 'L_A1_ROI',
 25: 'L_PSL_ROI',
 26: 'L_SFL_ROI',
 27: 'L_PCV_ROI',
 28: 'L_STV_ROI',
 29: 'L_7Pm_ROI',
 30: 'L_7m_ROI',
 31: 'L_POS1_ROI',
 32: 'L_23d_ROI',
 33: 'L_v23ab_ROI',
 34: 'L_d23ab_ROI',
 35: 'L_31pv_ROI',
 36: 'L_5m_ROI',
 37: 'L_5mv_ROI',
 38: 'L_23c_ROI',
 39: 'L_5L_ROI',
 40: 'L_24dd_ROI',
 41: 'L_24dv_ROI',
 42: 'L_7AL_ROI',
 43: 'L_SCEF_ROI',
 44: 'L_6ma_ROI',
 45: 'L_7Am_ROI',
 46: 'L_7PL_ROI',
 47: 'L_7PC_ROI',
 48: 'L_LIPv_ROI',
 49: 'L_VIP_ROI',
 50: 'L_MIP_ROI',
 51: 'L_1_ROI',
 52: 'L_2_ROI',
 53: 'L_3a_ROI',
 54: 'L_6d_ROI',
 55: 'L_6mp_ROI',
 56: 'L_6v_ROI',


In [48]:
L_labels.darrays[0].data

array([ 54,  49,  41, ..., 122, 122, 122], dtype=int32)

In [67]:
dd1 = np.load('../Documents/narratives/pp_pieman_plots/qaeac_L_0.npy')
dd2 = np.load('../Documents/narratives/pp_pieman_plots/qaaac_L_0.npy')
dd3 = np.load('../Documents/narratives/pp_pieman_plots/qapmc_L_0.npy')
dd4 = np.load('../Documents/narratives/pp_pieman_plots/qatpoj_L_0.npy')
dd5 = np.load('../Documents/narratives/pp_pieman_plots/qaLAN_L_0.npy')
#dd6 = np.load('../Documents/narratives/pp_pieman_plots/crvis_L_1.npy')

In [60]:
print(np.min(dd1), np.min(dd2), np.min(dd3), np.min(dd4), np.min(dd5))

0.7490959451738888 0.6584685124599631 0.6020546273925178 0.606138463549338 0.6948833862466628


In [66]:
print(np.min(dd1), np.min(dd2), np.min(dd3), np.min(dd4), np.min(dd5))

0.8278018896503817 0.7547248454412525 0.6826334426731123 0.6799748839804594 0.7590449257831225


In [68]:
print(np.min(dd1), np.min(dd2), np.min(dd3), np.min(dd4), np.min(dd5))

0.920548684770449 0.8258442848411084 0.7378346851595015 0.7519592388156517 0.7622720421580068


In [50]:
LH = np.zeros([L_labels.darrays[0].data.shape[0]])
print(LH.shape)

(40962,)


In [51]:
AAC_Lindices = [175, 125, 128, 129, 130, 176, 123, 107]
LANG_indices = [12, 26, 74, 75, 79, 81]
PMC_indices = [15, 30, 31, 33, 34, 35, 161]
EAC = {"A1": 24,
           "LBelt": 174,
           "MBelt": 173,
           "PBelt": 124,
           "RI": 104}
Tpoj_indices = [139, 140, 141, 28, 25]
#Vis_indices = [1, 4, 5, 6, 153, 154, 142, 160]

In [52]:
LH[np.where((L_labels.darrays[0].data==175) | (L_labels.darrays[0].data==125)
                                 | (L_labels.darrays[0].data==128) | (L_labels.darrays[0].data==129)
                                 | (L_labels.darrays[0].data==130) | (L_labels.darrays[0].data==176)
                                 | (L_labels.darrays[0].data==123) | (L_labels.darrays[0].data==107))[0]]=dd2

LH[np.where((L_labels.darrays[0].data==139) | (L_labels.darrays[0].data==140)
                                 | (L_labels.darrays[0].data==141) | (L_labels.darrays[0].data==28)
                                 | (L_labels.darrays[0].data==25))[0]]=dd4

LH[np.where((L_labels.darrays[0].data==12) | (L_labels.darrays[0].data==26)
                                 | (L_labels.darrays[0].data==74) | (L_labels.darrays[0].data==75)
                                 | (L_labels.darrays[0].data==79) | (L_labels.darrays[0].data==81)
                                 )[0]]=dd5

LH[np.where((L_labels.darrays[0].data==15) | (L_labels.darrays[0].data==30)
                                 | (L_labels.darrays[0].data==31) | (L_labels.darrays[0].data==33)
                                 | (L_labels.darrays[0].data==34) | (L_labels.darrays[0].data==35) |
                                (L_labels.darrays[0].data==161)
                                 )[0]]=dd3

LH[np.where((L_labels.darrays[0].data==24) | (L_labels.darrays[0].data==174)
                                 | (L_labels.darrays[0].data==173) | (L_labels.darrays[0].data==124)
                                 | (L_labels.darrays[0].data==104)
                                 )[0]]=dd1

In [42]:
fsaverage.keys()

dict_keys(['area_left', 'area_right', 'curv_left', 'curv_right', 'infl_left', 'infl_right', 'pial_left', 'pial_right', 'sphere_left', 'sphere_right', 'sulc_left', 'sulc_right', 'thick_left', 'thick_right', 'white_left', 'white_right', 'description'])

In [289]:
fsaverage['infl_left']

'/home/subbainria/nilearn_data/fsaverage6/infl_left.gii.gz'

In [ ]:
#surf_contrast = group_contrast[atlas["labels_L"]]
plotting.view_surf(fsaverage['infl_left'],
                   LH,threshold=0.001,
                   vmax=1.5, cmap='jet', symmetric_cmap=False)

In [63]:
ff1 = np.load('../Documents/narratives/pp_pieman_plots/ppeac_R_0.npy')
ff2 = np.load('../Documents/narratives/pp_pieman_plots/ppaac_R_0.npy')
ff3 = np.load('../Documents/narratives/pp_pieman_plots/pppmc_R_0.npy')
ff4 = np.load('../Documents/narratives/pp_pieman_plots/pptpoj_R_0.npy')
ff5 = np.load('../Documents/narratives/pp_pieman_plots/ppLAN_R_0.npy')
ff6 = np.load('../Documents/narratives/pp_pieman_plots/ppvis_R_0.npy')

In [64]:
print(np.min(ff1), np.min(ff2), np.min(ff3), np.min(ff4), np.min(ff5))

0.698328890290877 0.6213896481859531 0.62140833348387 0.6346798693037462 0.6407240484271107


In [62]:
print(np.min(ff1), np.min(ff2), np.min(ff3), np.min(ff4), np.min(ff5))

0.745709303419028 0.725129731836258 0.6444152803794108 0.6874696317118634 0.7042839587129845


In [56]:
RH = np.zeros([R_labels.darrays[0].data.shape[0]])
print(RH.shape)
RH[np.where((R_labels.darrays[0].data==175) | (R_labels.darrays[0].data==125)
                                 | (R_labels.darrays[0].data==128) | (R_labels.darrays[0].data==129)
                                 | (R_labels.darrays[0].data==130) | (R_labels.darrays[0].data==176)
                                 | (R_labels.darrays[0].data==123) | (R_labels.darrays[0].data==107))[0]]=ff2
RH[np.where((R_labels.darrays[0].data==139) | (R_labels.darrays[0].data==140)
                                 | (R_labels.darrays[0].data==141) | (R_labels.darrays[0].data==28)
                                 | (R_labels.darrays[0].data==25))[0]]=ff4
RH[np.where((R_labels.darrays[0].data==12) | (R_labels.darrays[0].data==26)
                                 | (R_labels.darrays[0].data==74) | (R_labels.darrays[0].data==75)
                                 | (R_labels.darrays[0].data==79) | (R_labels.darrays[0].data==81)
                                 )[0]]=ff5
RH[np.where((R_labels.darrays[0].data==15) | (R_labels.darrays[0].data==30)
                                 | (R_labels.darrays[0].data==31) | (R_labels.darrays[0].data==33)
                                 | (R_labels.darrays[0].data==34) | (R_labels.darrays[0].data==35) |
                                (R_labels.darrays[0].data==161)
                                 )[0]]=ff3
RH[np.where((R_labels.darrays[0].data==24) | (R_labels.darrays[0].data==174)
                                 | (R_labels.darrays[0].data==173) | (R_labels.darrays[0].data==124)
                                 | (R_labels.darrays[0].data==104)
                                 )[0]]=ff1

(40962,)


In [57]:
#surf_contrast = group_contrast[atlas["labels_L"]]
plotting.view_surf(fsaverage['infl_right'],
                   RH,threshold=0.001,
                   vmax=1.5, cmap='jet', symmetric_cmap=False)